In [1]:
%cd ../..
from inference_diffusion import StyleTTS2

import librosa
import IPython.display as ipd
import torch.cuda

device = 'cuda' if torch.cuda.is_available() else 'cpu'
#device = 'cpu'

d:\Project\TTS\Experimental\StyleTTS2-lite


[nltk_data] Downloading package punkt_tab to
[nltk_data]     C:\Users\catto\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


### Load G2P

If you did not use eSpeak for your language, please add your own G2P.

In [2]:
import sys
import phonemizer
if sys.platform.startswith("win"):
    try:
        from phonemizer.backend.espeak.wrapper import EspeakWrapper
        import espeakng_loader
        EspeakWrapper.set_library(espeakng_loader.get_library_path())
    except Exception as e:
        print(e)

def get_phoneme(text, lang):
    try:
        my_phonemizer = phonemizer.backend.EspeakBackend(language=lang, preserve_punctuation=True,  with_stress=True, language_switch='remove-flags')
        return my_phonemizer.phonemize([text])[0]
    except Exception as e:
        print(e)

In [3]:
from phonemizer.backend.espeak.wrapper import EspeakWrapper
import espeakng_loader
EspeakWrapper.set_library(espeakng_loader.get_library_path())

### Load models

In [4]:
config_path = "Configs/config.yaml"
models_path = "Models/Finetune/test_weight.pth"

### Synthesize speech

Little Note: Reference audio has a huge impact on the result. It is best to select audio around 10s long and consistent in both tone and speed.

In [5]:
speaker = {
    "path": "./Demo/Audio/2592.wav",  #Ref audio path
    "speed": 1.0,                        #Speaking speed
}

max_samples = 24000*20 #max 20 seconds ref audio
print(speaker['path'])
wave, sr = librosa.load(speaker['path'], sr=24000)
audio, index = librosa.effects.trim(wave, top_db=30)
if sr != 24000:              audio = librosa.resample(audio, sr, 24000)
if len(audio) > max_samples: audio = audio[:max_samples]
display(ipd.Audio(audio, rate=24000, normalize=True))

./Demo/Audio/2592.wav


In [19]:
text = '''
Ngày xửa ngày xưa, tại một ngôi làng nhỏ nằm bên rìa rừng Thâm Uyên, có một cô bé tên là Linh. Linh không xinh đẹp như nàng công chúa trong truyện cổ, cũng chẳng giỏi võ nghệ như các hiệp sĩ, nhưng cô có một trí óc sắc sảo và một trái tim nhân hậu.

Mỗi ngày, Linh giúp mẹ bán bánh ở chợ, chăm sóc em trai bị ốm yếu. Dù cuộc sống khó khăn, cô bé chưa bao giờ than vãn. Một buổi chiều mùa thu, khi đang hái nấm trong rừng, Linh phát hiện một chiếc đồng hồ cát bằng pha lê. Linh tò mò, xoay ngược đồng hồ. Lập tức, mọi vật xung quanh hóa thành sương mù và khi tan đi, cô thấy mình đang đứng trong cung điện nơi mẹ cô là hoàng hậu và chính cô là công chúa.

Cuộc sống giàu sang, nhưng Linh cảm thấy có gì đó không ổn. Dù có đủ đầy, cô không còn thấy mẹ cười thật lòng, em trai thì lại không sinh ra vì trong thế giới này mẹ không còn là người bán bánh. Những người nghèo ngoài cung điện bị đối xử lạnh nhạt và điều tệ nhất là cô cảm thấy chính mình đang dần trở nên ích kỷ, tàn nhẫn.
'''

| Parameter      | Type   | Description                                                                 | Performance Impact                                |
|----------------|--------|-----------------------------------------------------------------------------|----------------------------------------------------|
| `avg_style`     | BOOL   | Split the reference audio and calculate the average speaking style.        | Higher computation during style extraction         |
| `denoise`       | FLOAT  | Adjusts denoiser strength; range [0, 1].                                   | Additional computation for style processing        |
| `stabilize`     | BOOL   | Stabilizes speaking speed for long-form synthesis.                         | Slight additional computation                      |
| `n_merge`       | INT    | Avoids short sentences by merging if words < `n_merge`.                   | Higher VRAM usage as value increases               |


In [7]:
model = StyleTTS2(config_path, 
                  models_path
                ).eval().to(device)


Found: 189 symbols


c:\Users\catto\anaconda3\Lib\site-packages\torch\nn\utils\weight_norm.py:143: FutureWarning: `torch.nn.utils.weight_norm` is deprecated in favor of `torch.nn.utils.parametrizations.weight_norm`.
  WeightNorm.apply(module, name, dim)
c:\Users\catto\anaconda3\Lib\site-packages\torch\nn\modules\rnn.py:123: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.2 and num_layers=1
  warnings.warn(


decoder : 54289492
predictor : 16194612
text_encoder : 5612032
style_encoder : 13845440
diffusion : 10110656

Total : 100052232


In [21]:
avg_style         = False
denoise           = 0.2
stabilize         = False    
n_merge           = 44

with torch.no_grad():
    phonemes = get_phoneme(text=text, lang="vi")
    styles  = model.get_styles(speaker, denoise, avg_style)
    r       = model.generate(phonemes, styles, n_merge, stabilize, use_diffusion=False)

print('Synthesized:')
display(ipd.Audio(r, rate=24000, normalize=True))

Computing the style for: ./Demo/Audio/2592.wav
Generating Audio...
Synthesized:


In [ ]:
avg_style         = False
denoise           = 0.2
stabilize         = False    
n_merge           = 4

steps             = 18
embedding_scale   = 1.2
with torch.no_grad():
    phonemes = get_phoneme(text=text, lang="vi")
    styles  = model.get_styles(speaker, denoise, avg_style)
    r       = model.generate(phonemes, styles, steps, embedding_scale, n_merge, stabilize, use_diffusion=True)

print('Synthesized:')
display(ipd.Audio(r, rate=24000, normalize=True))

Computing the style for: ./Demo/Audio/2592.wav
Generating Audio...
Synthesized:


In [10]:
# avg_style         = False
# denoise           = 0.0
# stabilize         = False    
# n_merge           = 20
# with torch.no_grad():
#     phonemes = get_phoneme(text=text, lang="vi")
#     styles  = model.get_styles(speaker, denoise, avg_style)
#     r       = model.generate(phonemes, styles, n_merge, stabilize)

# print('Synthesized:')
# display(ipd.Audio(r, rate=24000, normalize=True))

Optional: The styles tensor can be saved and re-use later for faster generation time.

In [11]:
# model.save_styles(save_dir="./style1.pt")
# model.load_styles(save_dir="./style1.pt")

In [12]:
# with torch.no_grad():
#     phonemes = get_phoneme(text=text, lang="en-us")
#     styles  = model.get_styles(speaker, load_styles=True)
#     r       = model.generate(phonemes, styles, stabilize, n_merge)

# print('Synthesized:')
# display(ipd.Audio(r, rate=24000, normalize=True))